In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from skforecast.model_selection import backtesting_forecaster
from skforecast.ForecasterAutoreg import ForecasterAutoreg

import plotly
import plotly.graph_objects as go


from astral import LocationInfo
from astral.sun import sun


In [2]:
from custom_utils import *

In [3]:
data_path = "./../data/"
file_name = "data.csv"
data = pd.read_csv(data_path + file_name)
data = first_preprocess(data, data_path)
data.head()

d:\RA_work\timeseries_data\notebooks\custom_utils.py:157: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  data = data.asfreq("H")
d:\RA_work\timeseries_data\notebooks\custom_utils.py:83: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  data[column] = data[column].interpolate(method="linear", limit_direction="both")


space_heating  hot_water   sockets  lighting  \
datetime                                                                  
2021-01-01 00:00:00+00:00       3.425193   0.000000  0.049433  0.154873   
2021-01-01 01:00:00+00:00       4.012907   0.000000  0.047753  0.154846   
2021-01-01 02:00:00+00:00       5.342417   0.444782  0.051869  0.154997   
2021-01-01 03:00:00+00:00       5.756598   0.000000  0.043028  0.154626   
2021-01-01 04:00:00+00:00       5.415492   0.000000  0.050306  0.154498   

                           bld_engcons  car_chargers  weekend  bank_holiday  \
datetime                                                                      
2021-01-01 00:00:00+00:00     3.629499           0.0        0             1   
2021-01-01 01:00:00+00:00     4.215506           0.0        0             1   
2021-01-01 02:00:00+00:00     5.994066           0.0        0             1   
2021-01-01 03:00:00+00:00     5.954252           0.0        0             1   
2021-01-01 04:00:00+00:00     5.620296           0.0        0             1   

                           day_of_month  year  ...  sine_month  cos_month  \
datetime                                       ...                          
2021-01-01 00:00:00+00:00             1  2021  ...         0.5   0.866025   
2021-01-01 01:00:00+00:00             1  2021  ...         0.5   0.866025   
2021-01-01 02:00:00+00:00             1  2021  ...         0.5   0.866025   
2021-01-01 03:00:00+00:00             1  2021  ...         0.5   0.866025   
2021-01-01 04:00:00+00:00             1  2021  ...         0.5   0.866025   

                           sine_day_of_week  cos_day_of_week  \
datetime                                                       
2021-01-01 00:00:00+00:00         -0.974928        -0.222521   
2021-01-01 01:00:00+00:00         -0.974928        -0.222521   
2021-01-01 02:00:00+00:00         -0.974928        -0.222521   
2021-01-01 03:00:00+00:00         -0.974928        -0.222521   
2021-01-01 04:00:00+00:00         -0.974928        -0.222521   

                           sine_forecast_winddirection  \
datetime                                                 
2021-01-01 00:00:00+00:00                     0.000000   
2021-01-01 01:00:00+00:00                     0.000000   
2021-01-01 02:00:00+00:00                     0.000000   
2021-01-01 03:00:00+00:00                    -0.382683   
2021-01-01 04:00:00+00:00                    -0.382683   

                           cos_forecast_winddirection  sine_sunrise_hour  \
datetime                                                                   
2021-01-01 00:00:00+00:00                     1.00000           0.866025   
2021-01-01 01:00:00+00:00                     1.00000           0.866025   
2021-01-01 02:00:00+00:00                     1.00000           0.866025   
2021-01-01 03:00:00+00:00                     0.92388           0.866025   
2021-01-01 04:00:00+00:00                     0.92388           0.866025   

                           cos_sunrise_hour  sine_sunset_hour  cos_sunset_hour  
datetime                                                                        
2021-01-01 00:00:00+00:00              -0.5          0.866025             -0.5  
2021-01-01 01:00:00+00:00              -0.5          0.866025             -0.5  
2021-01-01 02:00:00+00:00              -0.5          0.866025             -0.5  
2021-01-01 03:00:00+00:00              -0.5          0.866025             -0.5  
2021-01-01 04:00:00+00:00              -0.5          0.866025             -0.5  

[5 rows x 32 columns]

In [4]:
data.columns

Index(['space_heating', 'hot_water', 'sockets', 'lighting', 'bld_engcons',
       'car_chargers', 'weekend', 'bank_holiday', 'day_of_month', 'year',
       'forecast_temperature', 'forecast_feelslike', 'forecast_weathertype',
       'forecast_windspeed', 'forecast_uvindex',
       'forecast_precipitationprobability', 'forecast_visibility',
       'week_of_year', 'daylight_hours', 'is_daylight', 'sine_hour',
       'cos_hour', 'sine_month', 'cos_month', 'sine_day_of_week',
       'cos_day_of_week', 'sine_forecast_winddirection',
       'cos_forecast_winddirection', 'sine_sunrise_hour', 'cos_sunrise_hour',
       'sine_sunset_hour', 'cos_sunset_hour'],
      dtype='object')

### Space heating model

In [5]:
exo_columns = ['forecast_temperature', 'forecast_feelslike', 'forecast_weathertype',
       'forecast_windspeed', 'forecast_uvindex',
       'forecast_precipitationprobability', 'forecast_visibility',
       'week_of_year', 'daylight_hours', 'is_daylight', 'sine_hour',
       'cos_hour', 'sine_month', 'cos_month', 'sine_day_of_week',
       'cos_day_of_week', 'sine_forecast_winddirection',
       'cos_forecast_winddirection', 'sine_sunrise_hour', 'cos_sunrise_hour',
       'sine_sunset_hour', 'cos_sunset_hour']
endo_columns = ['weekend', 'bank_holiday', 'day_of_month', 'year']
target_column = ["y"]
column_name = exo_columns + endo_columns  + target_column # + ["space_heating"]
test_date = '2023-01-01'

# transform the data
sh_data = data.copy()
# sh_data = sh_data.rename(columns={"space_heating": "y"})
sh_data["y"] = sh_data["space_heating"].shift(1)
sh_data = sh_data.dropna(axis=0)
sh_data_scaler, sh_transformed_data = create_std_scaler(sh_data, column_name[:-1])
sh_target_scaler, sh_transformed_target_data = create_std_scaler(sh_data, column_name[-1])

sh_transformed_data = pd.merge(sh_transformed_data, sh_transformed_target_data,
                               left_index=True,
                               right_index=True)

# # Training and testing data for comms and services
sh_train_data = sh_transformed_data[sh_transformed_data.index < test_date][column_name]
sh_test_data = sh_transformed_data[sh_transformed_data.index >= test_date][column_name]
sh_train_data.shape, sh_test_data.shape

                              columns          mean    variance  scale_factor
0                forecast_temperature  1.184490e+01   21.640482      4.651933
1                  forecast_feelslike  9.345162e+00   29.479648      5.429516
2                forecast_weathertype  6.297747e+00   23.408046      4.838186
3                  forecast_windspeed  1.508575e+01   50.911348      7.135219
4                    forecast_uvindex  1.080635e+00    2.562376      1.600742
5   forecast_precipitationprobability  1.954846e+01  732.856386     27.071320
6                 forecast_visibility  4.683930e+00    0.690008      0.830667
7                        week_of_year  2.657160e+01  226.533622     15.051034
8                      daylight_hours  0.000000e+00    0.000000      1.000000
9                         is_daylight  0.000000e+00    0.000000      1.000000
10                          sine_hour -1.625685e-17    0.500019      0.707120
11                           cos_hour -3.805320e-05    0.499981 

((17519, 27), (8760, 27))

In [6]:
def custom_metric(y_true, y_pred):
    '''
    Calculate the mean squared error using only the predicted values of the last
    3 months of the year.
    '''
    return calculate_smape(actual=y_true, predicted=y_pred)

In [7]:
main_data = pd.concat([sh_train_data, sh_test_data], axis=0)
main_data.shape

(26279, 27)

In [8]:
def plot_predictions(plot_data, title_text):
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=plot_data["time"].to_numpy(), y=plot_data["y"].to_numpy(),
                        mode='lines+markers',
                        name='actual'))
    fig.add_trace(go.Scatter(x=plot_data["time"].to_numpy(), y=plot_data["pred"].to_numpy(),
                        mode='lines+markers',
                        name='predictions'))
    fig.update_layout(title_text=title_text)
    fig.show()

#### Back testing on training

In [9]:
forecaster = ForecasterAutoreg(regressor = LinearRegression(), lags = 24)

In [10]:
forecaster.fit(
    y=sh_train_data['y'],
    exog=sh_train_data[exo_columns + endo_columns]
)

In [11]:
metric, predictions_training = backtesting_forecaster(
    forecaster         = forecaster,
    y                  = sh_train_data['y'],
    exog               = sh_train_data[exo_columns + endo_columns],
    steps              = 1,
    metric             = custom_metric,
    initial_train_size = None,
    refit              = False,
    n_jobs             = 'auto',
    verbose            = False,
    show_progress      = True
)

print(f"Backtest error: {metric:.2f}")
predictions_training.head()

  0%|          | 0/17495 [00:00<?, ?it/s]

Backtest error: 40.34


pred
2021-01-02 01:00:00+00:00  2.114290
2021-01-02 02:00:00+00:00  2.885574
2021-01-02 03:00:00+00:00  3.493571
2021-01-02 04:00:00+00:00  3.425004
2021-01-02 05:00:00+00:00  2.166095

In [12]:
predictions_training["y"] = sh_train_data["y"]
predictions_training = predictions_training.reset_index(drop=0)
predictions_training = predictions_training.rename(columns={"index": "time"})
predictions_training[["pred", "y"]] = sh_target_scaler.inverse_transform(predictions_training[["pred", "y"]])
predictions_training.head()

time      pred         y
0 2021-01-02 01:00:00+00:00  3.431411  4.270514
1 2021-01-02 02:00:00+00:00  4.347013  5.554376
2 2021-01-02 03:00:00+00:00  5.068774  5.039684
3 2021-01-02 04:00:00+00:00  4.987377  2.626135
4 2021-01-02 05:00:00+00:00  3.492909  5.677475

In [13]:
plot_predictions(predictions_training, title_text="Training data")

#### Back testing on training and testing with refit

In [14]:
metric, predictions = backtesting_forecaster(
    forecaster         = forecaster,
    y                  = main_data['y'],
    exog               = main_data[exo_columns + endo_columns],
    steps              = 1,
    metric             = custom_metric,
    initial_train_size = main_data[main_data.index < "2023-01-01"].shape[0],
    refit              = True,
    n_jobs             = 'auto',
    verbose            = False,
    show_progress      = True
)

print(f"Backtest error: {metric:.2f}")
predictions.head()

c:\Users\akson\anaconda3\envs\ra_env\Lib\site-packages\skforecast\model_selection\model_selection.py:474: LongTrainingWarning:

The forecaster will be fit 8760 times. This can take substantial amounts of time. If not feasible, try with `refit = False`.
 
 You can suppress this warning using: warnings.simplefilter('ignore', category=LongTrainingWarning)



  0%|          | 0/8760 [00:00<?, ?it/s]

Backtest error: 44.67


pred
2023-01-01 00:00:00+00:00 -0.279880
2023-01-01 01:00:00+00:00 -0.207919
2023-01-01 02:00:00+00:00  1.478830
2023-01-01 03:00:00+00:00  1.341316
2023-01-01 04:00:00+00:00  0.882951

In [15]:
predictions["y"] = main_data[main_data.index >= "2023-01-01"]["y"]
predictions = predictions.reset_index(drop=0)
predictions = predictions.rename(columns={"index": "time"})
predictions[["pred", "y"]] = sh_target_scaler.inverse_transform(predictions[["pred", "y"]])
plot_predictions(predictions, title_text="Testing data: actual vs predictions")

#### Metrics

In [16]:
cal_metrics(predictions_training["pred"].to_numpy(), predictions_training["y"].to_numpy())

MAE   MAPE  R2_Score  SMAPE     nRMSE      RMSE  MASE
0  0.29072  53.81  0.745643  40.67  0.076172  0.556221 -0.29

In [17]:
cal_metrics(predictions["pred"].to_numpy(), predictions["y"].to_numpy())

MAE   MAPE  R2_Score  SMAPE     nRMSE      RMSE  MASE
0  0.266229  26.19  0.716066  25.53  0.085336  0.504305 -0.27

In [18]:
main_data.columns

Index(['forecast_temperature', 'forecast_feelslike', 'forecast_weathertype',
       'forecast_windspeed', 'forecast_uvindex',
       'forecast_precipitationprobability', 'forecast_visibility',
       'week_of_year', 'daylight_hours', 'is_daylight', 'sine_hour',
       'cos_hour', 'sine_month', 'cos_month', 'sine_day_of_week',
       'cos_day_of_week', 'sine_forecast_winddirection',
       'cos_forecast_winddirection', 'sine_sunrise_hour', 'cos_sunrise_hour',
       'sine_sunset_hour', 'cos_sunset_hour', 'weekend', 'bank_holiday',
       'day_of_month', 'year', 'y'],
      dtype='object')

#### Building Data pred 1

In [30]:
building_data = pd.DataFrame({
    "time": predictions_training["time"].to_list() + predictions["pred"].to_list(),
    "space_heating_predictions": predictions_training["pred"].to_list() + predictions["pred"].to_list()
})

building_data.head()

time  space_heating_predictions
0  2021-01-02 01:00:00+00:00                   0.188870
1  2021-01-02 02:00:00+00:00                   0.188828
2  2021-01-02 03:00:00+00:00                   0.188828
3  2021-01-02 04:00:00+00:00                   0.188828
4  2021-01-02 05:00:00+00:00                   0.188870

### Others model

#### Backtesting on others ( lighting + hotwater + sockets ) data

In [20]:
exo_columns = ['forecast_temperature', 'forecast_feelslike', 'forecast_weathertype',
       'forecast_windspeed', 'forecast_uvindex',
       'forecast_precipitationprobability', 'forecast_visibility',
       'week_of_year', 'daylight_hours', 'is_daylight', 'sine_hour',
       'cos_hour', 'sine_month', 'cos_month', 'sine_day_of_week',
       'cos_day_of_week', 'sine_forecast_winddirection',
       'cos_forecast_winddirection', 'sine_sunrise_hour', 'cos_sunrise_hour',
       'sine_sunset_hour', 'cos_sunset_hour']
endo_columns = ['weekend', 'bank_holiday', 'day_of_month', 'year', "others"]
target_column = ["y"]
column_name = exo_columns + endo_columns  + target_column
test_date = '2023-01-01'

# transform the data
others_data = data.copy()
# "hot_water", "sockets", "lighting"
others_data["others"] = others_data["hot_water"] + others_data["sockets"] + others_data["lighting"]

others_data["y"] = others_data["others"].shift(1)
others_data = others_data.dropna(axis=0)

others_data.head()

others_data_scaler, others_transformed_data = create_std_scaler(others_data, column_name[:-1])
others_target_scaler, others_transformed_target_data = create_std_scaler(others_data, column_name[-1])

others_transformed_data = pd.merge(others_transformed_data, others_transformed_target_data,
                               left_index=True,
                               right_index=True)

# # Training and testing data for comms and services
train_data = others_transformed_data[others_transformed_data.index < test_date][column_name]
test_data = others_transformed_data[others_transformed_data.index >= test_date][column_name]
train_data.shape, test_data.shape

                              columns          mean    variance  scale_factor
0                forecast_temperature  1.184490e+01   21.640482      4.651933
1                  forecast_feelslike  9.345162e+00   29.479648      5.429516
2                forecast_weathertype  6.297747e+00   23.408046      4.838186
3                  forecast_windspeed  1.508575e+01   50.911348      7.135219
4                    forecast_uvindex  1.080635e+00    2.562376      1.600742
5   forecast_precipitationprobability  1.954846e+01  732.856386     27.071320
6                 forecast_visibility  4.683930e+00    0.690008      0.830667
7                        week_of_year  2.657160e+01  226.533622     15.051034
8                      daylight_hours  0.000000e+00    0.000000      1.000000
9                         is_daylight  0.000000e+00    0.000000      1.000000
10                          sine_hour -1.625685e-17    0.500019      0.707120
11                           cos_hour -3.805320e-05    0.499981 

((17519, 28), (8760, 28))

In [21]:
others_main_data = pd.concat([train_data, test_data], axis=0)
others_main_data.shape

(26279, 28)

In [22]:
params = {
    'n_estimators': 100,
    'criterion':  'absolute_error',
    'max_depth': 2,
    'random_state': 994564,
    "max_features": "log2",
    'verbose': 0
}
forecaster = ForecasterAutoreg(
    regressor=RandomForestRegressor(**params), 
    lags=24
)
forecaster.fit(
    y=train_data["y"],
    exog=train_data[exo_columns + endo_columns]
)

In [23]:
metric, predictions_training = backtesting_forecaster(
    forecaster         = forecaster,
    y                  = train_data['y'],
    exog               = train_data[exo_columns + endo_columns],
    steps              = 1,
    metric             = custom_metric,
    initial_train_size = None,
    refit              = False,
    n_jobs             = 'auto',
    verbose            = False,
    show_progress      = True
)

print(f"Backtest error: {metric:.2f}")
predictions_training.head()

  0%|          | 0/17495 [00:00<?, ?it/s]

Backtest error: 67.91


pred
2021-01-02 01:00:00+00:00 -0.532040
2021-01-02 02:00:00+00:00 -0.532114
2021-01-02 03:00:00+00:00 -0.532114
2021-01-02 04:00:00+00:00 -0.532114
2021-01-02 05:00:00+00:00 -0.532040

In [24]:
predictions_training["y"] = train_data["y"]
predictions_training = predictions_training.reset_index(drop=0)
predictions_training = predictions_training.rename(columns={"index": "time"})
predictions_training[["pred", "y"]] = others_target_scaler.inverse_transform(predictions_training[["pred", "y"]])
predictions_training.head()

time      pred         y
0 2021-01-02 01:00:00+00:00  0.188870  0.653082
1 2021-01-02 02:00:00+00:00  0.188828  0.195995
2 2021-01-02 03:00:00+00:00  0.188828  0.197053
3 2021-01-02 04:00:00+00:00  0.188828  0.630013
4 2021-01-02 05:00:00+00:00  0.188870  0.197586

In [25]:
plot_predictions(predictions_training, title_text="Others Training data")

#### Backtesting others model with refit

In [26]:
metric, predictions = backtesting_forecaster(
    forecaster         = forecaster,
    y                  = others_main_data['y'],
    exog               = others_main_data[exo_columns + endo_columns],
    steps              = 1,
    metric             = custom_metric,
    initial_train_size = others_main_data[others_main_data.index < "2023-01-01"].shape[0],
    refit              = True,
    n_jobs             = 'auto',
    verbose            = False,
    show_progress      = True
)

print(f"Backtest error: {metric:.2f}")
predictions.head()

c:\Users\akson\anaconda3\envs\ra_env\Lib\site-packages\skforecast\model_selection\model_selection.py:474: LongTrainingWarning:

The forecaster will be fit 8760 times. This can take substantial amounts of time. If not feasible, try with `refit = False`.
 
 You can suppress this warning using: warnings.simplefilter('ignore', category=LongTrainingWarning)



  0%|          | 0/8760 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [ ]:
predictions["y"] = others_main_data["y"]
predictions = predictions.reset_index(drop=0)
predictions = predictions.rename(columns={"index": "time"})
predictions[["pred", "y"]] = others_target_scaler.inverse_transform(predictions[["pred", "y"]])
predictions.head()

In [ ]:
plot_predictions(predictions, title_text="Others Test data")

#### Metrics

In [ ]:
cal_metrics(predictions["pred"].to_numpy(), predictions["y"].to_numpy())

In [ ]:
cal_metrics(predictions_training["pred"].to_numpy(), predictions_training["y"].to_numpy())

#### Building data pred 2

In [ ]:
building_data["others_predictions"] = predictions_training["pred"].to_list() + predictions["pred"].to_list()

building_data.head()

In [ ]:
building_data.to_csv("sh_oth_preds.csv", index=False)